# **Visualize burned areas by tile and date**


### **Install Earth Engine API & Folium**

In [1]:
%%capture
!pip install earthengine-api --upgrade
!pip install folium

### **Prevent re-import errors**

In [1]:
%load_ext autoreload
%autoreload 2

### **Imports**

In [2]:
from IPython.core.display import display
import numpy as np
import folium
import json
import ast
import os
import ee

### **Sign-in to Google Earth Engine**

In [3]:
ee.Authenticate()
try:
  ee.Initialize()
  print("Earth Engine initilized successfully!")
except ee.EEException as e:
  print("Earth Engine could not be initialized!")


Successfully saved authorization token.
Earth Engine initilized successfully!


## **Read data**

### **Tiles**

In [4]:
def getLandTiles():
    allTiles = []
    with open('../data/tiles/allTiles.txt', 'r') as file:
        for line in file.readlines():
            allTiles.append(ast.literal_eval(line))
    print(f'{len(allTiles)} total tiles retrieved')

    waterProportion = 0.50
    landTiles = [tile for tile in allTiles if tile[1] < waterProportion]
    print(f'{len(landTiles)} tiles retrieved with less than {waterProportion*100:.0f}% water area')
    return landTiles
    
# 2D dictionary like dict[long][lat]
def makeFireDictionary():
    fireData = {}
    for tile in getLandTiles():
        longitude = str(tile[0][0])
        latitude  = str(tile[0][1])
        if longitude in fireData:
            fireData[longitude][latitude] = None
        else:
            fireData[longitude] = {}
            fireData[longitude][latitude] = None
    return fireData


### **Get FireData JSONs**

In [5]:
#get JSON data files sorted from oldest to newest data
datadir = '../data/burn/'
files = sorted(os.listdir(datadir))


#combine all into dictionary
data = makeFireDictionary()
for idx, file in enumerate(files):
    with open(os.path.join(datadir,file)) as f:
        temp = json.load(f)
        if 'dates' in temp: del temp['dates']
        for k, v in temp.items():
            data[k].update((k2,v2) for k2, v2 in temp[k].items() if v2 is not None)

fireCount = 0
for k in data.keys():
    fireCount += len([x for x in data[k].values() if x is not None])
print(f'{fireCount} land tiles have fire data')

9016 total tiles retrieved
6910 tiles retrieved with less than 50% water area
2715 land tiles have fire data


### **Flatten 2D dict to list of fire data tiles**

In [6]:
#flatten to array like [ [(long, lat), date], [(long,lat), None], ...]
tData = []
for k,v in data.items():
    tData.extend([[(k, k2), v2] for k2, v2 in data[k].items()])

#maps a date to a float (0, 1] from newest to oldest date
dates = sorted(list(set([item[1] for item in tData if item[1] is not None])))
colorMap = dict(map(lambda x: (x[1], (x[0]+1)/len(dates)), enumerate(dates)))

#convert dates to
coloredData = []
for tup in tData:
    longitude = tup[0][0]
    latitude  = tup[0][1]
    date = tup[1]

    #oldest = white, newest = red
    opacity = 0
    if date is not None:
        opacity = colorMap[date]
    coloredData.append([(longitude, latitude), opacity])

### **Build the map**
#### **Opaque tiles are newer burns, transparent tiles are older burns**

In [7]:
# map design
tile = {'tile':'https://stamen-tiles-{s}.a.ssl.fastly.net/terrain-background/{z}/{x}/{y}{r}.png',
                'attr': 'Map tiles by <a href="http://stamen.com">Stamen Design</a>, <a href="http://creativecommons.org/licenses/by/3.0">CC BY 3.0</a> &mdash; Map data &copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors'}

# define map
fMap = folium.Map(location=[37.5010, -122.1899], zoom_start=10,
                    tiles = tile['tile'],
                    attr = tile['attr'])
for tup in coloredData:
    sw_long = float(tup[0][0])
    sw_lat  = float(tup[0][1])
    opacity   = tup[1]

    #draw tiles
    folium.Rectangle(
        bounds=[(sw_lat, sw_long), (sw_lat+0.1, sw_long+0.1)],
        color='#ff0000',
        opacity=0,
        fill=True,
        fill_color='#ff0000',
        fill_opacity=opacity
    ).add_to(fMap)

### **Visualize and save**

In [8]:
display(fMap)
fMap.save('../outputs/tiledBurnMap.html')